In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import datetime
from datetime import date

In [2]:
df = pd.read_csv('airquality.csv')

## Preprocessing

In [3]:
df.head()

site_id                       site  country   site_type       site_area  \
0  at0ill1  Illmitz am Neusiedler See  austria  background  rural_regional   
1  at0ill1  Illmitz am Neusiedler See  austria  background  rural_regional   
2  at0ill1  Illmitz am Neusiedler See  austria  background  rural_regional   
3  at0ill1  Illmitz am Neusiedler See  austria  background  rural_regional   
4  at0ill1  Illmitz am Neusiedler See  austria  background  rural_regional   

   elevation        date    pm10   pm2.5     no2      o3    so2  
0      117.0  2023-01-01  18.279  16.070   6.234  28.100  0.380  
1      117.0  2023-01-02  13.359  12.360   9.243  24.121  0.339  
2      117.0  2023-01-03  11.934  10.135  17.199  16.999  0.404  
3      117.0  2023-01-04   8.834   7.792   6.280  50.592  0.408  
4      117.0  2023-01-05   5.947   5.075   4.881  69.127  0.383

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24530 entries, 0 to 24529
Data columns (total 12 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   site_id    24530 non-null  object 
 1   site       23805 non-null  object 
 2   country    23805 non-null  object 
 3   site_type  23805 non-null  object 
 4   site_area  23805 non-null  object 
 5   elevation  23805 non-null  float64
 6   date       24530 non-null  object 
 7   pm10       23349 non-null  float64
 8   pm2.5      21913 non-null  float64
 9   no2        24364 non-null  float64
 10  o3         21388 non-null  float64
 11  so2        21133 non-null  float64
dtypes: float64(6), object(6)
memory usage: 2.2+ MB


In [5]:
df['date'] = pd.to_datetime(df['date'])
df['country'] = df['country'].str.title()
df['site'] = df['site'].str.title()
df['o3'] = df['o3'].round(1)
df = df.drop(columns=['elevation', 'pm10', 'pm2.5','no2', 'so2'])
df

site_id                       site   country   site_type  \
0      at0ill1  Illmitz Am Neusiedler See   Austria  background   
1      at0ill1  Illmitz Am Neusiedler See   Austria  background   
2      at0ill1  Illmitz Am Neusiedler See   Austria  background   
3      at0ill1  Illmitz Am Neusiedler See   Austria  background   
4      at0ill1  Illmitz Am Neusiedler See   Austria  background   
...        ...                        ...       ...         ...   
24525  pt03083                 Laranjeiro  Portugal  background   
24526  pt03083                 Laranjeiro  Portugal  background   
24527  pt03083                 Laranjeiro  Portugal  background   
24528  pt03083                 Laranjeiro  Portugal  background   
24529  pt03083                 Laranjeiro  Portugal  background   

            site_area       date    o3  
0      rural_regional 2023-01-01  28.1  
1      rural_regional 2023-01-02  24.1  
2      rural_regional 2023-01-03  17.0  
3      rural_regional 2023-01-04  50.6  
4      rural_regional 2023-01-05  69.1  
...               ...        ...   ...  
24525           urban 2023-12-27  27.1  
24526           urban 2023-12-28  25.5  
24527           urban 2023-12-29  21.2  
24528           urban 2023-12-30  26.2  
24529           urban 2023-12-31  19.9  

[24530 rows x 7 columns]

In [6]:
site_ids_with_null = df[df['o3'].isna()]['site_id'].value_counts()
print(site_ids_with_null)

site_id
hu0027a    365
hu0045a    365
gr0003a    364
dehh068    362
dehh015    362
hu0057a    361
nl00553    358
nl00551    358
pl0209a     25
at60170     23
it0908a     19
betr222     14
fr14012     12
pt03063     12
betn043     10
nl00014     10
betn085      9
pt03072      9
gr0038a      8
hu0022a      8
pt03083      8
at32701      8
it1827a      7
nl00012      7
betn060      6
es1269a      5
pl0138a      5
at31401      4
deub004      4
es1271a      3
pl0212a      3
at4s416      3
pl0194a      3
betn132      3
betr001      3
desn025      3
it0461a      3
nl00444      2
pl0175a      2
nl00644      1
pl0136a      1
it0459a      1
at4s406      1
hu0034a      1
at0ill1      1
Name: count, dtype: int64


In [7]:
filtered_site_ids = site_ids_with_null[site_ids_with_null > 350]
filtered_site_ids.index

Index(['hu0027a', 'hu0045a', 'gr0003a', 'dehh068', 'dehh015', 'hu0057a',
       'nl00553', 'nl00551'],
      dtype='object', name='site_id')

In [8]:
df = df[~df['site_id'].isin(filtered_site_ids)]
df['site_id'].nunique()

68

## First visualization

In [9]:
fig = px.scatter(df, x="date", y="o3", color=df['o3'] > 100,
                 color_discrete_sequence=["lightgrey", "orange"],
                  labels={"color": "Exceeded Dates"},
                  hover_data={
                    'country':True,  
                    'site_id':True,
                    'date':True,
                    'o3':True,
                    'site': True,     
                    'site_area': True, 
        })

fig.update_traces(
    customdata=df[['country','site_id', 'site', 'site_area']].values,
    hovertemplate="<b>Country:</b> %{customdata[0]}<br>" +
                  "<b>Site ID:</b> %{customdata[1]}<br>" +
                  "<b>Site:</b> %{customdata[2]}<br>" +
                  "<b>Site area:</b> %{customdata[3]}<br>" +
                  "<b>Date:</b> %{x}<br>" +
                  "<b>O3 value:</b> %{y} µg/m³<extra></extra>"
)

fig.add_shape(
    type="line",
    x0=df['date'].min(),
    x1=df['date'].max(),
    y0=100,
    y1=100,
    line=dict(color="red", width=2, dash="dash"),
    name="Threshold 100"
)

fig.add_annotation(
    x=df['date'].max() - pd.Timedelta(days=22),
    y=100 + 8,
    text="Limits (WHO)",
    showarrow=False,
    font=dict(color="red", size=12),
    align="right"
)

fig.add_shape(
    type="line",
    x0=df['date'].min(),
    x1=df['date'].max(),
    y0=120,
    y1=120,
    line=dict(color="darkblue", width=2, dash="dash"),
    name="Threshold 120"
)

fig.add_annotation(
    x=df['date'].max() - pd.Timedelta(days=35),
    y=120 + 8,
    text="Limits (EU - until 2029)",
    showarrow=False,
    font=dict(color="darkblue", size=12),
    align="left"
)

fig.add_annotation(
    x=df['date'].max() - pd.Timedelta(days=280),
    y=190,
    text="During summer heat waves, higher temperatures <br>and sunlight generally cause an increase in ozone<br>pollutant levels, particularly in urban areas",
    showarrow=False,
    font=dict(color="orange", size=12, style="italic"),
    align="left"
)


fig.add_annotation(
    x=-0.005,
    y=1.1,
    text="Even under the EU standards, which are far less strict than WHO standards, the current situation remains highly concerning",
    showarrow=False,
    font=dict(size=14, color="black"),
    align="center",
    xref="paper",
    yref="paper"
)

fig.add_annotation(
    x=-0.005,
    y=-0.12,
    text="Daily ozone levels (µg/m³) measured at 68 sites across 11 European countries",
    showarrow=False,
    font=dict(size=12, color="darkblue"),
    align="center",
    xref="paper",
    yref="paper"
)

x_range = pd.date_range("2023-01-01", "2024-01-01", freq="MS")

for i in range(len(x_range) - 1):
    midpoint = x_range[i] + (x_range[i + 1] - x_range[i]) / 2
    fig.add_annotation(
        x=midpoint,
        y=-0.05,
        text=x_range[i].strftime('%b'),
        showarrow=False,
        font=dict(size=12, color="black"),
        align="center",
        xref="x",
        yref="paper"
    )

fig.update_layout(
    title="Summer 2023: Europe dramatically exceeded ozone pollution limits",
    title_font=dict(
        size=18,
        color="darkblue",
        weight='bold'
    ),
    xaxis_title="",
    yaxis_title="",
    xaxis=dict(
        range=[pd.Timestamp("2023-01-01"), pd.Timestamp("2023-12-31")],
        tickvals=x_range,
        tickformat="%b",
        tickmode="array",
        tickangle=0,
        showgrid=True,
        gridcolor='lightblue',
        showticklabels=False,
    ),  
    yaxis=dict(
        range=[0, df['o3'].max() * 1.1],
        showgrid=False,
    ),
    showlegend=False,
    margin=dict(t=80, l=60, r=40, b=60),
    width=1000,
    height=500,
    title_x=0.059,
    title_y=0.95,
    title_xanchor='left',
    title_yanchor='top',
    plot_bgcolor="white"
)

fig.show()


## Second Visualization

In [10]:
df100 = df[df.o3 >= 100]
df100_grouped = df100.groupby(['country', 'site_id', 'site', 'site_area'])['o3'].count().reset_index(name='num_exceeded_dates_100')
df100_grouped.head()

country  site_id                            site       site_area  \
0  Austria  at0ill1       Illmitz Am Neusiedler See  rural_regional   
1  Austria  at31401               Mödling Bachgasse        suburban   
2  Austria  at32701  Schwechat Sportplatz,Mühlgasse        suburban   
3  Austria  at4s406               Wels Linzerstraße        suburban   
4  Austria  at4s416                  Linz Neue Welt        suburban   

   num_exceeded_dates_100  
0                     101  
1                      66  
2                      74  
3                      68  
4                      48

In [11]:
df100 = df[df.o3 >= 100]
df100_grouped = df100.groupby(['country', 'site_id', 'site', 'site_area'])['o3'].count().reset_index(name='num_exceeded_dates_100')
country_totals = df100_grouped.groupby('country')['num_exceeded_dates_100'].sum().reset_index(name='total_exceeded_dates_per_country')
df100_grouped = df100_grouped.merge(country_totals, on='country')
df100_grouped = df100_grouped.sort_values(by=['total_exceeded_dates_per_country','num_exceeded_dates_100'], ascending=[False, False])
df100_grouped = df100_grouped.reset_index(drop=True)
df100_grouped['country'] = df100_grouped['country'].replace({'Austria': '<b>Austria<br>(6 sites)</b>', 'Italy': '<b>Italy<br>(6 sites)</b>', 'Germany': 'Germany<br>(7 sites)',
                                 'Portugal': '<b>Portugal<br>(6 sites)</b>', 'Poland': 'Poland<br>(5 sites)', 'Greece': 'Greece<br>(5 sites)',
                                 'Belgium': '<b>Belgium<br>(6 sites)</b>', 'France': 'France<br>(5 sites)', 'Hungary': 'Hungary<br>(3 sites)',
                                 'Spain': 'Spain<br>(5 sites)', 'Netherlands': 'Netherlands<br>(3 sites)'})

df100_grouped.head(10)

country  site_id                            site  \
0  <b>Austria<br>(6 sites)</b>  at0ill1       Illmitz Am Neusiedler See   
1  <b>Austria<br>(6 sites)</b>  at32701  Schwechat Sportplatz,Mühlgasse   
2  <b>Austria<br>(6 sites)</b>  at4s406               Wels Linzerstraße   
3  <b>Austria<br>(6 sites)</b>  at31401               Mödling Bachgasse   
4  <b>Austria<br>(6 sites)</b>  at4s416                  Linz Neue Welt   
5  <b>Austria<br>(6 sites)</b>  at60170          Graz Süd Tiergartenweg   
6    <b>Italy<br>(6 sites)</b>  it1773a   Genga -Parco Gola Della Rossa   
7    <b>Italy<br>(6 sites)</b>  it1827a               Ancona Cittadella   
8    <b>Italy<br>(6 sites)</b>  it2096a              Bz6 Via Amba Alagi   
9    <b>Italy<br>(6 sites)</b>  it0908a                          Bormio   

        site_area  num_exceeded_dates_100  total_exceeded_dates_per_country  
0  rural_regional                     101                               398  
1        suburban                      74                               398  
2        suburban                      68                               398  
3        suburban                      66                               398  
4        suburban                      48                               398  
5        suburban                      41                               398  
6  rural_regional                      87                               328  
7           urban                      75                               328  
8           urban                      75                               328  
9           urban                      51                               328

In [12]:
fig = px.bar(
    df100_grouped,
    x="country", 
    y='num_exceeded_dates_100', 
    color='country',
    text = 'site_id',
    color_discrete_map={'Greece<br>(5 sites)': 'orange', '<b>Austria<br>(6 sites)</b>': 'darkblue', '<b>Italy<br>(6 sites)</b>': 'darkblue', 
                        '<b>Portugal<br>(6 sites)</b>': 'darkblue', '<b>Belgium<br>(6 sites)</b>':'darkblue',
                        'France<br>(5 sites)':'lightgrey', 'Germany<br>(7 sites)':'lightgrey', 'Poland<br>(5 sites)':'lightgrey', 
                        'Hungary<br>(3 sites)':'lightgrey', 'Spain<br>(5 sites)':'lightgrey', 'Netherlands<br>(3 sites)':'lightgrey'},
    labels={"color": "Exceeded Dates"},
    hover_data={
        'site_id':True,
        'site': True,
        'site_area': True,
        'num_exceeded_dates_100': True,
    }
)

fig.update_traces(
    hovertemplate=(
        "<b>Site ID:</b> %{customdata[0]}<br>" +
        "<b>Site:</b> %{customdata[1]}<br>" +
        "<b>Site area:</b> %{customdata[2]}<br>" +
        "<b>Number of exceeded dates:</b> %{y}<extra></extra>"
    )
)

fig.add_annotation(
    x=0.43,
    y=400,
    text="Austria has the worst ozone pollution in 2023 <br>among countries with six sites considered",
    showarrow=True,
    ax=40,
    ay=-8,
    font=dict(color="darkblue", size=12),
    xanchor='left',
    align="left"
)

fig.add_annotation(
    x=5,
    y=235,
    text="Greece has the site with the most exceeded dates in 2023<br>and the widest variation between sites",
    showarrow=True,
    ax=10,
    ay=-40,
    font=dict(color="orange", size=12),
    xanchor='left',
    align="left"
)

fig.add_annotation(
    x=6.85,
    y=380,
    text="The minimal lack of data at most sites, and <br>the complete absence of data at certain sites <br>(hu0045a, hu0027a, gr0003a, dehh068, <br>dehh015, hu0057a, nl00553, nl00551) limits <br>the accuracy of the overall comparison",
    showarrow=False,
    font=dict(color="black", size=12, style="italic"),
    xanchor='left',
    align="left"
)

fig.add_annotation(
    x=0,
    y=-0.13,
    text = "Number of exceeded dates per country and site when applying WHO standards, with up to 3 exceedances permitted per year",
    showarrow=False,
    font=dict(size=12, color="darkblue"),
    align="center",
    xref="paper",
    yref="paper"
)

fig.update_traces(
    textposition='inside',
    insidetextanchor='middle'
)

fig.update_layout(
    barmode='stack', xaxis={'categoryorder':'total descending'},
    title="As for exceedance levels, the distribution and quantity vary across European countries",
    title_font=dict(
        size=18,
        color="darkblue",
        weight='bold'
    ),
    xaxis_title="",
    yaxis_title="",
    yaxis_showgrid=False,
    margin=dict(t=70, l=60, r=40, b=80),
    width=1000,
    height=600,
    title_x=0.059,
    title_y=0.95,
    title_xanchor='left',
    title_yanchor='top',
    plot_bgcolor="white",
    showlegend=False
)

fig.show()


## Third Visualization (optional)
For this part, I use the package calplot (https://pypi.org/project/plotly-calplot/). If the visualization cannot be displayed, the issue may lie with the numpy package. Please try using an older version (between 1.22.3 and 2.0.0).

In [13]:
#%pip install plotly-calplot

In [14]:
gr0020a = df.loc[df['site_id'] == 'gr0020a'][['date','o3']].copy()
gr0020a = gr0020a.reset_index(drop=True)
gr0020a.head()

date    o3
0 2023-01-01  42.1
1 2023-01-02  28.5
2 2023-01-03  26.1
3 2023-01-04  46.0
4 2023-01-05  18.6

In [15]:
from plotly_calplot import calplot

fig = calplot(gr0020a, x='date', y="o3", colorscale="spectral_r", 
              month_lines_color="grey", showscale=True)

fig.add_annotation(
    x=0,
    y=-0.28,
    text="A year in ozone: 2023 daily concentrations (µg/m³) at Kordelio (gr0020) site, Greece",
    showarrow=False,
    font=dict(size=12, color="darkblue"),
    align="center",
    xref="paper",
    yref="paper"
)

fig.add_annotation(
    x=-0.005,
    y=1.2,
    text="Taking action against global warming can lower ozone levels, improve air quality and protect against respiratory diseases",
    showarrow=False,
    font=dict(size=14, color="black"),
    align="left",
    xref="paper",
    yref="paper"
)

fig.update_layout(
    barmode='stack',
    hovermode=False,
    title="At the worst-affected area, ozone pollution remains hazardous for nearly half the year",
    title_font=dict(
        size=18,
        color="darkblue",
        weight='bold'
    ),
    xaxis=dict(
        title="",
        tickformat="%b",
        ticktext=[date(1900, i, 1).strftime("%b") for i in range(1, 13)],
        tickfont=dict(size=12, color="black")
    ),
    yaxis=dict(
        title="",
        tickfont=dict(size=12, color="black")
    ),
    yaxis_showgrid=False,
    margin=dict(t=60, l=50, r=40, b=50),
    width=1000,
    height=250,
    title_x=0.059,
    title_y=0.95,
    title_xanchor='left',
    title_yanchor='top',
    plot_bgcolor="white",
    showlegend=False
)

fig.show()